# Description

This notebook will use the outputs from the HAPPY software to perform the following operations:

1. Extract the fundamental HR per scan
2. Compute the aliased HR frequency per scan
3. Save scan-wise HR into to ```Resources/HR_scaninfo.csv```
4. Check for statistical differences in HR across scan types (i.e., drowsy vs. awake)
5. Check for statistical differences in aliased HR across scan types (i.e., drowsy vs. awake)
6. Check for statistical differences in amplitude of cardiac traces across scan types and segment types

### Import Libraries

In [1]:
import pandas as pd
import numpy  as np
import hvplot.pandas
import holoviews as hv
import matplotlib.pyplot as plt
import seaborn as sns
import os.path as osp
import json

from utils.basics import get_available_runs, load_segments, aliased_freq
from utils.variables import DATA_DIR, Resources_Dir

from scipy.signal import get_window, spectrogram, welch
from scipy.stats import kruskal, wilcoxon, ttest_ind, mannwhitneyu
from scipy.signal import find_peaks

from bokeh.models.formatters import DatetimeTickFormatter
formatter = DatetimeTickFormatter(minutes = ['%Mmin:%Ssec'])

### Load Scan Lists

We will now load the list of scans that are used in the main part of the analyses. For each scan we also have their label: "drowsy" or "awake"

In [2]:
Drowsy_scans = get_available_runs(when='final',type='drowsy')
Awake_scans  = get_available_runs(when='final',type='awake')
All_scans    = get_available_runs(when='final',type='all')
print('++ INFO: Total number of scans:  %d' % len(All_scans))
print('++ INFO: Number of Drowsy scans: %d' % len(Drowsy_scans))
print('++ INFO: Number of Awake scans:  %d' % len(Awake_scans))

++ INFO: Total number of scans:  404
++ INFO: Number of Drowsy scans: 194
++ INFO: Number of Awake scans:  210


### Load HAPPY-estimated Cardiac Traces (25hz) into a Dataframe

In a previous notebook, we estiamted cardiac traces for each resint-state scan using the "happy" software. We now load these into a pandas dataframe. The extracted traces have a sampling frequency of 25Hz. The resulting dataframe will have a time index based on this frquency. It will also have one column per scan containing the stimated cardiac traces

In [3]:
# Create Time Delta Index
cardiac_25hz_df_index = pd.timedelta_range(start='0 s', end='900 s', periods=((900*25)-1))
cardiac_25hz_df_index.shape

(22499,)

In [4]:
%%time
cardiac_25hz_df = pd.DataFrame(columns=All_scans,index=cardiac_25hz_df_index)
for scanID in All_scans:
    aux_sbj, aux_run = scanID.split('_',1)
    # Load Cardiac Trace
    aux_data_path = osp.join(DATA_DIR, aux_sbj, aux_run, '{run}_orig.happy'.format(run=aux_run),'{run}_orig.happy_desc-stdrescardfromfmri_timeseries.tsv'.format(run=aux_run))
    aux_json_path = osp.join(DATA_DIR, aux_sbj, aux_run, '{run}_orig.happy'.format(run=aux_run),'{run}_orig.happy_desc-stdrescardfromfmri_timeseries.json'.format(run=aux_run))
    # Load Json File
    with open(aux_json_path) as json_file:
        aux_json = json.load(json_file)
    # Load Data
    aux_data         = pd.read_csv(aux_data_path,sep='\t', header=None)
    aux_data.columns = aux_json['Columns']
    # Load Sampling Frequency
    aux_fs = aux_json['SamplingFrequency']
    #Add to DF
    cardiac_25hz_df[scanID] = aux_data['cardiacfromfmri_dlfiltered_25.0Hz'].values

CPU times: user 16.3 s, sys: 3.63 s, total: 20 s
Wall time: 20.2 s


In [5]:
cardiac_25hz_df.head()

100610_rfMRI_REST3_PA  100610_rfMRI_REST4_AP  \
0 days 00:00:00                         1.639751               1.302338   
0 days 00:00:00.040003555               1.366537               1.593729   
0 days 00:00:00.080007111               0.422834               0.916655   
0 days 00:00:00.120010667               0.321943               0.921103   
0 days 00:00:00.160014223               0.525089               0.953989   

                           104416_rfMRI_REST3_PA  105923_rfMRI_REST3_PA  \
0 days 00:00:00                        -0.813308              -0.852783   
0 days 00:00:00.040003555              -0.774033               0.211101   
0 days 00:00:00.080007111               0.019407               0.160859   
0 days 00:00:00.120010667              -0.148790               0.367900   
0 days 00:00:00.160014223              -0.106943               0.812550   

                           105923_rfMRI_REST4_AP  111312_rfMRI_REST1_PA  \
0 days 00:00:00                         1.471923               1.422951   
0 days 00:00:00.040003555               1.092474               0.462556   
0 days 00:00:00.080007111               0.422061               0.009611   
0 days 00:00:00.120010667               0.005156               0.125067   
0 days 00:00:00.160014223              -0.322726              -0.274042   

                           111312_rfMRI_REST3_PA  114823_rfMRI_REST2_AP  \
0 days 00:00:00                        -0.498370               1.519785   
0 days 00:00:00.040003555               0.064814               1.188727   
0 days 00:00:00.080007111               1.199880               0.403318   
0 days 00:00:00.120010667               0.872791               0.291075   
0 days 00:00:00.160014223               0.641826              -0.101927   

                           114823_rfMRI_REST4_AP  115017_rfMRI_REST4_AP  ...  \
0 days 00:00:00                         0.411759               0.667916  ...   
0 days 00:00:00.040003555               0.178208               0.601937  ...   
0 days 00:00:00.080007111              -0.033559              -0.004724  ...   
0 days 00:00:00.120010667               0.132649              -0.325410  ...   
0 days 00:00:00.160014223               0.219823              -0.495992  ...   

                           958976_rfMRI_REST1_PA  958976_rfMRI_REST2_AP  \
0 days 00:00:00                         0.129249               0.898043   
0 days 00:00:00.040003555               0.230003               1.642289   
0 days 00:00:00.080007111               0.286177               1.600638   
0 days 00:00:00.120010667               0.162202               0.926267   
0 days 00:00:00.160014223               0.068959               0.582462   

                           958976_rfMRI_REST3_PA  966975_rfMRI_REST1_PA  \
0 days 00:00:00                         0.172268               1.476832   
0 days 00:00:00.040003555               0.804565               1.109514   
0 days 00:00:00.080007111               1.334043               0.765427   
0 days 00:00:00.120010667               0.892026               0.881073   
0 days 00:00:00.160014223               0.499054               0.667884   

                           966975_rfMRI_REST2_AP  966975_rfMRI_REST3_PA  \
0 days 00:00:00                        -0.289019              -0.964227   
0 days 00:00:00.040003555              -0.413618              -1.084485   
0 days 00:00:00.080007111              -0.699529              -0.399990   
0 days 00:00:00.120010667              -0.885222              -0.556222   
0 days 00:00:00.160014223              -1.032898              -0.258466   

                           966975_rfMRI_REST4_AP  971160_rfMRI_REST2_AP  \
0 days 00:00:00                         1.897792               0.436671   
0 days 00:00:00.040003555               1.868436               0.658296   
0 days 00:00:00.080007111               0.751035              -0.131252   
0 days 00:00:00.120010667               0.846738              -0.538272   
0 days 00:00:0

***
# Scan-wise Analyses

First, we will explore potential differences in cardiac function at the scan level (i.e. drowsy vs. awake scans). Later in the notebook we will conduct similar analyses at the segment level (EO vs. EC).

#### Estimate Spectrogram for each Trace, extract average HR, and aliased freq

1. Compute the spectrogram of cardiac traces using the whole scan.
2. Find the fundamental frequency (e.g., cardiac frequency)
3. Compute its aliased equivalent based on the fMRI sampling frequency

The next figure a few cells below exemplifies this process.

In [6]:
fs_card = 25 # Hz (Frequency in standarized HAPPY outputs)
fs_fmri = 1  # Hz (TR in fMRI data)

In [7]:
%%time
cardiac_welch_df = pd.DataFrame(columns=All_scans)
cardiac_hr_df = pd.DataFrame(index=All_scans, columns=['HR','HR_aliased','Scan Type'])
for scanID in All_scans:
    #wf, wc      = welch(cardiac_25hz_df[scanID], fs=fs_card, window=get_window(('tukey',0.25),256), noverlap=128, scaling='density', detrend='constant', nfft=1024)
    wf, wc      = welch(cardiac_25hz_df[scanID], fs=fs_card, window=get_window(('tukey',0.25),750), noverlap=375, scaling='density', detrend='constant', nfft=1024)
    
    cardiac_welch_df[scanID] = wc
    # Extract Average HR
    cardiac_hr_df.loc[scanID,'HR'] = wf[cardiac_welch_df[scanID].idxmax()]
    # Compute alisaed HR
    cardiac_hr_df.loc[scanID,'HR_aliased'] = aliased_freq(fs_fmri,cardiac_hr_df.loc[scanID,'HR'] )
    #n                                      = round(cardiac_hr_df.loc[scanID,'HR'] / float(fs_fmri))
    #cardiac_hr_df.loc[scanID,'HR aliased'] = abs(fs_fmri * n - cardiac_hr_df.loc[scanID,'HR'])
    # Add Scan Type
    if scanID in Awake_scans:
        cardiac_hr_df.loc[scanID,'Scan Type'] = 'Awake'
    if scanID in Drowsy_scans:
        cardiac_hr_df.loc[scanID,'Scan Type'] = 'Drowsy'
    
cardiac_welch_df.index      = wf
cardiac_welch_df.index.name = 'Frequency [Hz]' 

CPU times: user 791 ms, sys: 17.5 ms, total: 808 ms
Wall time: 809 ms


#### Representative Figures with one scan (to explain method)

In [10]:
sample_scan = '995174_rfMRI_REST3_PA'
aux_sbj, aux_run = sample_scan.split('_',1)
# Load Cardiac Trace
aux_data_path = osp.join(DATA_DIR, aux_sbj, aux_run, '{run}_orig.happy'.format(run=aux_run),'{run}_orig.happy_desc-stdrescardfromfmri_timeseries.tsv'.format(run=aux_run))
aux_json_path = osp.join(DATA_DIR, aux_sbj, aux_run, '{run}_orig.happy'.format(run=aux_run),'{run}_orig.happy_desc-stdrescardfromfmri_timeseries.json'.format(run=aux_run))
# Load Json File
with open(aux_json_path) as json_file:
    aux_json = json.load(json_file)
# Load Data
aux_data         = pd.read_csv(aux_data_path,sep='\t', header=None)
aux_data.columns = aux_json['Columns']
# Udpate Index
aux_data.index  =  cardiac_25hz_df_index
aux_data.index.name = 'Time'

In [11]:
aux_data['cardiacfromfmri_dlfiltered_25.0Hz'].hvplot(c='k',width=1500,xformatter=formatter) + \
(cardiac_welch_df[sample_scan].hvplot(c='k', ylabel='Power Spectrum') * \
hv.Text(8,4,'HR = {hr:.2f} Hz --> HR_aliased = {hra:.2f} Hz'.format(hr=cardiac_hr_df.loc[sample_scan,'HR'],hra=cardiac_hr_df.loc[sample_scan,'HR_aliased'])))

:Layout
   .Curve.Cardiacfromfmri_dlfiltered_25_full_stop_0Hz :Curve   [Time]   (cardiacfromfmri_dlfiltered_25.0Hz)
   .Overlay.A_995174_rfMRI_REST3_PA                   :Overlay
      .Curve.A_995174_rfMRI_REST3_PA :Curve   [Frequency [Hz]]   (995174_rfMRI_REST3_PA)
      .Text.I                        :Text   [x,y]


#### Distribution of scan-level frequencies

**Cardiac Frequency Distribution**: Here is the distribution of estimated cardiac rates at the scan level. In red, we show what are normal ranges for resting cardiac rates (50bpm or 0.83 Hz <- -> 80bpm or 1.33 Hz). We can observe that with a few exception, estimated cardiac frequencies fall within tose normal ranges

In [12]:
hv.Rectangles([(50/60,0,80/60,10)]).opts(alpha=0.5, color='r') * \
cardiac_hr_df.reset_index(drop=True).infer_objects().hvplot.hist(y='HR', color='gray', bins=30, normed=True, title='(A) Distribution of Scan-Level Heart Rate',ylim=(0,5), xlim=(0,2)) * \
cardiac_hr_df.reset_index(drop=True).infer_objects().hvplot.kde( y='HR', color='gray', xlabel='Heart Rate [Hz]', ylabel='Density', fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}).opts(toolbar=None)

:Overlay
   .Rectangles.I   :Rectangles   [x0,y0,x1,y1]
   .Histogram.I    :Histogram   [HR]   (HR_frequency)
   .Distribution.I :Distribution   [HR]   (Density)

**Aliased Cardiac Frequency Distribution:** distribution of aliased cardiac frequencies. We can see that those overlap with the targeted range of frequencies of this study (in green).

In [13]:
hv.Rectangles([(0.03,0,0.07,10)]).opts(alpha=0.5, color='g') * \
cardiac_hr_df.reset_index(drop=True).infer_objects().hvplot.hist(y='HR_aliased', color='gray', bins=30, normed=True, title='(B) Distribution of Scan-Level Aliased Heart Rate', ylim=(0,10), xlim=(-.1,.8)) * \
cardiac_hr_df.reset_index(drop=True).infer_objects().hvplot.kde(y='HR_aliased', color='gray', xlabel='Aliased Heart Rate [Hz]', ylabel='Density', fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}, xlim=(-.1,.8)).opts(toolbar=None)

:Overlay
   .Rectangles.I   :Rectangles   [x0,y0,x1,y1]
   .Histogram.I    :Histogram   [HR_aliased]   (HR_aliased_frequency)
   .Distribution.I :Distribution   [HR_aliased]   (Density)

* Plot group differences in aliased HR across scan types 

In [14]:
cardiac_hr_df.reset_index(drop=True).infer_objects().hvplot.box(y='HR_aliased', by='Scan Type', title='(C) Aliased HR segregated by Scan Type', hover_cols=['Scan ID'], tools=['hover'],
                                                                fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}, ylabel='Aliased HR [Hz]', color='Scan Type', cmap=['orange','lightblue'], legend=False).opts(toolbar=None)

:BoxWhisker   [Scan Type]   (HR_aliased)

* Test for statistical differences in aliased HR at the group level

In [15]:
print('++ INFO: Statistical Tests for differences in HRa across scan types')
print('++ ================================================================')
awake_hrs  = cardiac_hr_df[cardiac_hr_df['Scan Type']=='Awake']['HR_aliased']
drowsy_hrs = cardiac_hr_df[cardiac_hr_df['Scan Type']=='Drowsy']['HR_aliased']
tt_s, tt_p = ttest_ind(    awake_hrs, drowsy_hrs, alternative='two-sided')
mw_s, mw_p = mannwhitneyu( awake_hrs, drowsy_hrs, alternative='two-sided')
kk_s, kk_p = kruskal(      awake_hrs, drowsy_hrs)
print('   T-Test                   [HRa EO different than EC] T    = %2.2f | p=%0.5f' % (tt_s, tt_p))
print('   Mann-Whitney U Rank Test [HRa EO different than EC] Stat = %2.2f | p=%0.5f' % (mw_s, mw_p))
print('   Kruskas-Wallis H Test    [HRa EO different than EC] Stat = %2.2f | p=%0.5f' % (kk_s, kk_p))

++ INFO: Statistical Tests for differences in HRa across scan types
++ ================================================================
   T-Test                   [HRa EO different than EC] T    = 1.27 | p=0.20570
   Mann-Whitney U Rank Test [HRa EO different than EC] Stat = 21507.00 | p=0.33182
   Kruskas-Wallis H Test    [HRa EO different than EC] Stat = 0.94 | p=0.33161


* Save scan-wise HR info to disk

In [16]:
path = osp.join(Resources_Dir,'HR_scaninfo.csv')
cardiac_hr_df.to_csv(path)
print('++ INFO: Save scan-wise HR info to disk [%s]' % path)
cardiac_hr_df.head()

++ INFO: Save scan-wise HR info to disk [/data/SFIMJGC_HCP7T/hcp7t_fv_sleep/Resources/HR_scaninfo.csv]


HR HR_aliased Scan Type
100610_rfMRI_REST3_PA  1.513672   0.486328     Awake
100610_rfMRI_REST4_AP  1.464844   0.464844     Awake
104416_rfMRI_REST3_PA  1.171875   0.171875     Awake
105923_rfMRI_REST3_PA  0.976562   0.023438     Awake
105923_rfMRI_REST4_AP  1.025391   0.025391     Awake

***
# Segment-wise Analyses

### Load segments longer than 60s (EO & EC)

In [17]:
segments = load_segments('all',min_dur=60)

++ INFO: segment_df has shape: (989, 8)


In [18]:
segments.columns = ['Run', 'Segment Type', 'Segment_Index', 'Segment_UUID', 'Onset', 'Offset', 'Duration', 'Scan_Type']

### Compute HR and aliased-HR per segment

In [19]:
%%time
hr_list, hr_alias_list = [],[]
for r,row in segments.iterrows():
    scanID    = row['Run']
    segID     = row['Segment_UUID']
    onset     = pd.Timedelta(int(row['Onset']), unit='s')
    offset    = pd.Timedelta(int(row['Offset']), unit='s')
    time_mask = (cardiac_25hz_df.index >=onset) & (cardiac_25hz_df.index <=offset)
    ts        = cardiac_25hz_df.loc[time_mask,scanID]
    wf, wc      = welch(ts, fs=fs_card, window=get_window(('tukey',0.25),750), noverlap=375, scaling='density', detrend='constant', nfft=1024)
    hr        = wf[wc.argmax()]
    # Compute aliased HR
    hr_alias  = aliased_freq(fs_fmri,hr)
    hr_list.append(hr)
    hr_alias_list.append(hr_alias)

segments['HR'] = hr_list
segments['HR_aliased'] = hr_alias_list

CPU times: user 865 ms, sys: 784 µs, total: 865 ms
Wall time: 867 ms


#### Save segment-wise HR info to disk

In [20]:
path = osp.join(Resources_Dir,'HR_segmentinfo.csv')
segments.to_csv(path)
print('++ INFO: Save scan-wise HR info to disk [%s]' % path)
segments.head()

++ INFO: Save scan-wise HR info to disk [/data/SFIMJGC_HCP7T/hcp7t_fv_sleep/Resources/HR_segmentinfo.csv]


Run Segment Type  Segment_Index  \
0  100610_rfMRI_REST3_PA           EO            0.0   
1  100610_rfMRI_REST3_PA           EO            1.0   
2  100610_rfMRI_REST3_PA           EO            2.0   
3  100610_rfMRI_REST3_PA           EO            3.0   
4  100610_rfMRI_REST3_PA           EO            4.0   

                           Segment_UUID  Onset  Offset  Duration Scan_Type  \
0  bf6b5ed0-d4b0-4f3a-a779-edbafbd6a408    0.0   173.0     173.0     Awake   
1  f9400e40-f910-4f17-9e14-d3786a3ca6ec  175.0   308.0     133.0     Awake   
2  d52abf9a-9dbf-40d9-80c2-2e9d01460244  310.0   476.0     166.0     Awake   
3  4558890a-2ec2-4543-badc-f91dc754dd4f  478.0   793.0     315.0     Awake   
4  18c528de-f209-457a-9f9f-5d14e14a6315  795.0   878.0      83.0     Awake   

         HR  HR_aliased  
0  1.513672    0.486328  
1  1.538086    0.461914  
2  1.538086    0.461914  
3  1.538086    0.461914  
4  1.513672    0.486328

In [21]:
hv.Rectangles([(50/60,0,80/60,10)]).opts(alpha=0.5, color='r') * \
segments.reset_index(drop=True).infer_objects().hvplot.hist(y='HR', color='gray', bins=30, normed=True, title='(D) Distribution of Segment-Level Heart Rate',ylim=(0,5), xlim=(0,2)) * \
segments.reset_index(drop=True).infer_objects().hvplot.kde( y='HR', color='gray', xlabel='Heart Rate [Hz]', ylabel='Density', fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}).opts(toolbar=None)

:Overlay
   .Rectangles.I   :Rectangles   [x0,y0,x1,y1]
   .Histogram.I    :Histogram   [HR]   (HR_frequency)
   .Distribution.I :Distribution   [HR]   (Density)

In [22]:
hv.Rectangles([(0.03,0,0.07,10)]).opts(alpha=0.5, color='g') * \
segments.reset_index(drop=True).infer_objects().hvplot.hist(y='HR_aliased', color='gray', bins=30, normed=True, title='(E) Distribution of Segment-Level Aliased Heart Rate', ylim=(0,10), xlim=(-.1,.8)) * \
segments.reset_index(drop=True).infer_objects().hvplot.kde(y='HR_aliased', color='gray', xlabel='Aliased Heart Rate [Hz]', ylabel='Density', fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}, xlim=(-.1,.8)).opts(toolbar=None)

:Overlay
   .Rectangles.I   :Rectangles   [x0,y0,x1,y1]
   .Histogram.I    :Histogram   [HR_aliased]   (HR_aliased_frequency)
   .Distribution.I :Distribution   [HR_aliased]   (Density)

In [23]:
segments.reset_index(drop=True).infer_objects().hvplot.box(y='HR_aliased', by='Segment Type', 
                                                           title='(F) Aliased HR segregated by Segment Type',fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}, 
                                                           ylabel='Aliased HR [Hz]', color='Segment Type', cmap=['orange','lightblue'], legend=False).opts(toolbar=None)

:BoxWhisker   [Segment Type]   (HR_aliased)

In [24]:
print('++ INFO: Statistical Tests for differences in HR across segment types')
print('++ ==================================================================')
eo_hrs = segments[segments['Segment Type']=='EO']['HR_aliased']
ec_hrs = segments[segments['Segment Type']=='EC']['HR_aliased']
tt_s, tt_p = ttest_ind(    eo_hrs, ec_hrs, alternative='two-sided')
mw_s, mw_p = mannwhitneyu( eo_hrs, ec_hrs, alternative='two-sided')
kk_s, kk_p = kruskal(      eo_hrs, ec_hrs)
print('   T-Test                   [HR EO different than EC] T    = %2.2f | p=%0.5f' % (tt_s, tt_p))
print('   Mann-Whitney U Rank Test [HR EO different than EC] Stat = %2.2f | p=%0.5f' % (mw_s, mw_p))
print('   Kruskas-Wallis H Test    [HR EO different than EC] Stat = %2.2f | p=%0.5f' % (kk_s, kk_p))

++ INFO: Statistical Tests for differences in HR across segment types
++ ==================================================================
   T-Test                   [HR EO different than EC] T    = 1.71 | p=0.08754
   Mann-Whitney U Rank Test [HR EO different than EC] Stat = 95061.00 | p=0.07782
   Kruskas-Wallis H Test    [HR EO different than EC] Stat = 3.11 | p=0.07780


***
# Scan-wise Cardiac Amplitude

In [25]:
cardiac_amp_df = pd.DataFrame(cardiac_25hz_df.std(),columns=['C_Amplitude'])
for scanID in All_scans:
    # Add Scan Type
    if scanID in Awake_scans:
        cardiac_amp_df.loc[scanID,'Scan Type'] = 'Awake'
    if scanID in Drowsy_scans:
        cardiac_amp_df.loc[scanID,'Scan Type'] = 'Drowsy'

In [26]:
cardiac_amp_df.reset_index(drop=True).infer_objects().hvplot.box(y='C_Amplitude', ylabel='Amplitude',
                                                                 by='Scan Type', 
                                                                 title='(G) Amplitude of Cardiac Signal by Scan Type',fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}, color='Scan Type', cmap=['orange','lightblue'], legend=False).opts(toolbar=None)

:BoxWhisker   [Scan Type]   (C_Amplitude)

In [32]:
print('++ INFO: Statistical Tests for differences in HR Amp across scan types')
print('++ ================================================================')
awake_amps  = cardiac_amp_df[cardiac_amp_df['Scan Type']=='Awake']['C_Amplitude']
drowsy_amps = cardiac_amp_df[cardiac_amp_df['Scan Type']=='Drowsy']['C_Amplitude']
tt_s, tt_p = ttest_ind(    awake_amps, drowsy_amps, alternative='two-sided')
mw_s, mw_p = mannwhitneyu( awake_amps, drowsy_amps, alternative='two-sided')
kk_s, kk_p = kruskal(      awake_amps, drowsy_amps)
print('   T-Test                   [HR Amp EO different than EC] T    = %2.2f | p=%0.5f' % (tt_s, tt_p))
print('   Mann-Whitney U Rank Test [HR Amp EO different than EC] Stat = %2.2f | p=%0.5f' % (mw_s, mw_p))
print('   Kruskas-Wallis H Test    [HR Amp EO different than EC] Stat = %2.2f | p=%0.5f' % (kk_s, kk_p))

++ INFO: Statistical Tests for differences in HR Amp across scan types
++ ================================================================
   T-Test                   [HR Amp EO different than EC] T    = 0.97 | p=0.33380
   Mann-Whitney U Rank Test [HR Amp EO different than EC] Stat = 20930.00 | p=0.63326
   Kruskas-Wallis H Test    [HR Amp EO different than EC] Stat = 0.23 | p=0.63295


***
# Segment-wise Amplitude

In [33]:
%%time
amp_list = []
for r,row in segments.iterrows():
    scanID    = row['Run']
    segID     = row['Segment_UUID']
    onset     = pd.Timedelta(int(row['Onset']), unit='s')
    offset    = pd.Timedelta(int(row['Offset']), unit='s')
    time_mask = (cardiac_25hz_df.index >=onset) & (cardiac_25hz_df.index <=offset)
    ts        = cardiac_25hz_df.loc[time_mask,scanID]
    amp_list.append(ts.std())
    
segments['C_Amplitude'] = amp_list

CPU times: user 452 ms, sys: 23 µs, total: 452 ms
Wall time: 452 ms


In [34]:
segments.reset_index(drop=True).infer_objects().hvplot.box(y='C_Amplitude', ylabel='Amplitude', hover_cols=['Run','Duration'], tools=['hover'],
                                                           by='Segment Type',
                                                           title='(H) Amplitude of Cardiac Signal by Segment Type',
                                                           fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}, color='Segment Type', cmap=['orange','lightblue'], legend=False).opts(toolbar=None)

:BoxWhisker   [Segment Type]   (C_Amplitude)

In [59]:
print('++ INFO: C_Amplitude for EO [mean +/- stdev] = %.2f +/- %.2f' % (segments.groupby(by='Segment Type').mean().loc['EO','C_Amplitude'],segments.groupby(by='Segment Type').std().loc['EO','C_Amplitude']))
print('++ INFO: C_Amplitude for EC [mean +/- stdev] = %.2f +/- %.2f' % (segments.groupby(by='Segment Type').mean().loc['EC','C_Amplitude'],segments.groupby(by='Segment Type').std().loc['EC','C_Amplitude']))

++ INFO: C_Amplitude for EO [mean +/- stdev] = 0.84 +/- 0.04
++ INFO: C_Amplitude for EC [mean +/- stdev] = 0.83 +/- 0.05


In [35]:
print('++ INFO: Statistical Tests for differences in HR across segment types')
print('++ ==================================================================')
eo_amps = segments[segments['Segment Type']=='EO']['C_Amplitude']
ec_amps = segments[segments['Segment Type']=='EC']['C_Amplitude']
tt_s, tt_p = ttest_ind(    eo_amps, ec_amps, alternative='two-sided')
mw_s, mw_p = mannwhitneyu( eo_amps, ec_amps, alternative='two-sided')
kk_s, kk_p = kruskal(      eo_amps, ec_amps)
print('   T-Test                   [HR Amp EO different than EC] T    = %2.2f | p=%0.5f' % (tt_s, tt_p))
print('   Mann-Whitney U Rank Test [HR Amp EO different than EC] Stat = %2.2f | p=%0.5f' % (mw_s, mw_p))
print('   Kruskas-Wallis H Test    [HR Amp EO different than EC] Stat = %2.2f | p=%0.5f' % (kk_s, kk_p))

++ INFO: Statistical Tests for differences in HR across segment types
++ ==================================================================
   T-Test                   [HR Amp EO different than EC] T    = 3.08 | p=0.00213
   Mann-Whitney U Rank Test [HR Amp EO different than EC] Stat = 97235.00 | p=0.01975
   Kruskas-Wallis H Test    [HR Amp EO different than EC] Stat = 5.43 | p=0.01974


In [31]:
segments.reset_index(drop=True).infer_objects().hvplot.kde(y='C_Amplitude', by='Segment Type', xlabel='Amplitude', 
                                                          fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}, color=['orange','lightblue']).opts(toolbar=None, legend_position='top_left')

:NdOverlay   [Segment Type]
   :Distribution   [C_Amplitude]   (Density)

In [32]:
cardiac_amp_df.reset_index(drop=True).infer_objects().hvplot.kde(y='C_Amplitude', by='Scan Type', xlabel='Amplitude', 
                                                          fontsize={'xticks':18,'yticks':18,'ylabel':18,'xlabel':18, 'title':18}, color=['orange','lightblue']).opts(toolbar=None, legend_position='top_left')

:NdOverlay   [Scan Type]
   :Distribution   [C_Amplitude]   (Density)

***
***
# END OF NOTEBOOK
***
***